# Example: Feature-centric analogous bars
* This notebook shows an application of the <b>feature-centric analogous bars method</b> to compare barcodes built on two different point clouds `P` and `Q`.

#### Feature-centric analogous bars
* <b> Inputs </b>
    * Distance matrix among points in `P`
    * Distance matrix among points in `Q`
    * Corss-system distance matrix among `P` and `Q`.
* <b> Goal </b>
    * Given a selected bar in the Vietoris-Rips barcode `barcode(VR(P))`, find its representations in `barcode(VR(Q))`
* <b> Implementation </b>:
    * User selects a bar of interest from `barcode(VR(P))`
    * The function `run_extension_VR_to_W_bar` finds the representation of the selected bar in the Witness complex `W(P,Q)`.
    * We then apply Dowker's theorem to find the corresponding cycle in `W(Q,P)`.
    * Lastly, we run the function `run_extension_W_to_VR_bar` to find the bar extension in `barcode(VR(Q))`.
    * Note that we don't provide an individual function for feature-centric analogous bars method. 
    * All extension methds are implemented component-wise with $\mathbb{F}_2$ coefficients. We assume that all bars of barcodes have unique death times. 
* <b> Comparison to Algorithm 6 of paper </b>
    * In the paper, we run the first extension method (from VR to W) and find the collection of all cycle extensions $E(\tau, W^\bullet_{P,Q})$. We then apply Dowker's Theorem to all such cycle extensions to find the collection $E(\tau, W^\bullet_{Q,P})$. For each cycle $[\sigma] \in E(\tau, W^\bullet_{Q,P})$, we run the second extension method (from W to VR).   
    * In our implementation, we don't apply the second extension method to the entire collection $E(\tau, W^\bullet_{Q,P})$ as this can require huge computation time. Instead, we allow the user to select a specific cycle in $E(\tau, W^\bullet_{P,Q})$ via `cycle_W_PQ`. We then find its corresponding cycle `cycle_W_QP` in $W^\bullet_{Q,P}$ via Dowker's Theorem and run the second extension method on `cycle_W_QP`. 
   

#### Example data 
* `Q`: Points sampled from a double torus
* `P`: Points sampled from a circle that loops around two of the S1's of Q.
* The goal is to understand how a feature in `P` is represented in `Q`

#### Contents 
1. Load points and visualize
2. Plot the four relevant barcodes
3. Run the extension method from VR to W
4. Apply Dowker's Theorem
5. Run the extension method from W to VR. 
6. Explore cycle extension & bar extension under fixed interval decompositions of `barcode(VR(Q))`.
7. Explore alternative bar extensions under all possible interval decompositions of `barcode(VR(Q))`.
8. Alternative parameter choice for second extension

In [1]:
using Revise
includet("../../../extension_method.jl")

HTML{String}("<script>\n// Immediately-invoked-function-expression to avoid global variables.\n(function() {\n    var warning_div = document.getElementById(\"webio-warning-16816990682408171994\");\n    var hide = function () {\n        var script = document.getElementById(\"webio-setup-15448037154809291033\");\n        var parent = script && script.parentElement;\n        var grandparent = parent && parent.parentElement;\n        if (grandparent) {\n            grandparent.style.display = \"none\";\n        }\n        warning_div.style.display = \"none\";\n    };\n    if (typeof Jupyter !== \"undefined\") {\n        console.log(\"WebIO detected Jupyter notebook environment.\");\n        // Jupyter notebook.\n        var extensions = (\n            Jupyter\n            && Jupyter.notebook.config.data\n            && Jupyter.notebook.config.data.load_extensions\n        );\n        if (extensions && extensions[\"webio-jupyter-notebook\"]) {\n            // Extension already loaded.\n            console.log(\"Jupyter WebIO nbextension detected; not loading ad-hoc.\");\n            hide();\n            return;\n        }\n    } else if (window.location.pathname.includes(\"/lab\")) {\n        // Guessing JupyterLa\n        console.log(\"Jupyter Lab detected; make sure the @webio/jupyter-lab-provider labextension is installed.\");\n        hide();\n        return;\n    }\n})();\n\n</script>\n<p\n    id=\"webio-warning-16816990682408171994\"\n    class=\"output_text output_stderr\"\n    style=\"padding: 1em; font-weight: bold;\"\n>\n    Unable to load WebIO. Please make sure WebIO works for your Jupyter client.\n    For troubleshooting, please see <a href=\"https://juliagizmos.github.io/WebIO.jl/latest/providers/ijulia/\">\n    the WebIO/IJulia documentation</a>.\n    <!-- TODO: link to installation docs. -->\n</p>\n")

┌ Warning: ORCA.jl has been deprecated and all savefig functionality
│ has been implemented directly in PlotlyBase itself.
│ 
│ By implementing in PlotlyBase.jl, the savefig routines are automatically
│ available to PlotlyJS.jl also.
└ @ ORCA /opt/julia/packages/ORCA/U5XaN/src/ORCA.jl:8


In [2]:
using .ext
using DelimitedFiles
using Distances
using HDF5
using Printf
using Eirene
using Plots
using JLD

# 1. Load points and visualize
* `Q`: points sampled from a double torus
* `P`: S1 sampled on the double torus

In [3]:
# load points
Q = double_torus = load("data.jld2", "double_torus")
P = circle = load("data.jld2", "circle")

n_Q = size(double_torus,1)
n_P = size(circle,1);

print("number of points in P: ", n_P, "\n")
print("number of points in Q: ", n_Q)

number of points in P: 78
number of points in Q: 731

Plot points 

In [5]:
p = plot_3D(P, Q, Q_markersize = 2, xlim = (-5, 5), ylim = (-5, 5), zlim = (-5, 5))

<!DOCTYPE html>
 
 
 Plots.jl

# 2. Plot the four relevant barcodes

Get distance matrices

In [6]:
# gather all points 
X = vcat(P, Q)

# compute distance
D = pairwise(Euclidean(), X, X, dims = 1)

# Define submatrices 
D_P = D[1:n_P, 1:n_P]
D_Q = D[n_P+1:end, n_P+1:end]
D_P_Q = D[1:n_P, n_P+1:end]
    # rows (landmarks): P1
    # columns (witness) : P2
D_Q_P = D[n_P+1:end, 1:n_P];
    # rows (landmarks): P2
    # columns (witness) : P1

Run persistence (this may take a while)

In [7]:
# Compute Vietoris-Rips persistence on two regions
dim = 1
VR_P = eirene(D_P, record = "all", maxdim = dim)
VR_Q = eirene(D_Q, record = "all", maxdim = dim)

# compute Witness persistence
W_P = compute_Witness_persistence(D_P_Q, maxdim = dim)
W_Q = compute_Witness_persistence(D_Q_P, maxdim = dim);

In [8]:
# plot all four barcodes
barcode_VR_P = barcode(VR_P, dim = 1)
barcode_W_P = barcode(W_P["eirene_output"], dim = 1)
barcode_W_Q = barcode(W_Q["eirene_output"], dim = 1)
barcode_VR_Q = barcode(VR_Q, dim = 1)

# plot
p1 = plot_barcode(barcode_VR_P, lw = 3, title = "Barcode(VR(P))", titlefontsize = 12)
p2 = plot_barcode(barcode_W_P, lw = 3, title = "Barcode(W(P,Q))", titlefontsize = 12)
p3 = plot_barcode(barcode_W_Q, lw = 3, title = "Barcode(W(Q,P))", titlefontsize = 12)
p4 = plot_barcode(barcode_VR_Q, lw = 2, title = "Barcode(VR(Q))", titlefontsize = 12)
plot(p1, p2, p3, p4, layout = grid(4,1), size = (500, 700))

<!DOCTYPE html>
 
 
 Plots.jl

# 3. Run the extension method from VR to W

Given the selected interval in `barcode(VR(P))`, find its cycle extensions in `W(P,Q)`

In [9]:
# select bar of interest
VR_P_class = 2

2

In [10]:
# plot cycle rep of selected bar
cycle = classrep(VR_P, class = VR_P_class, dim = 1)
cycle = [sort(cycle[:,i]) for i = 1:size(cycle,2)]
plot_cycle(P, Q, cycle = cycle)

<!DOCTYPE html>
 
 
 Plots.jl

In [11]:
# run extension method
extension_to_W_PQ = run_extension_VR_to_W_bar(C_VR = VR_P,
                                              D_VR = D_P,
                                              VR_bar = VR_P_class,
                                              W = W_P,
                                              D_W = D_P_Q);

### Find all cycle extensions

In [12]:
# find all cycle extensions
CE1, _ = find_CE_BE(extension_to_W_PQ);

In [13]:
param = extension_to_W_PQ["epsilon_0"]
CE1[param]

Dict{Any,Any} with 1 entry:
  0 => [[62, 72], [50, 61], [3, 37], [1, 8], [58, 59], [43, 53], [39, 60], [42,…

In [14]:
cycle_W_PQ = CE1[param][0];

In [15]:
# plot selected cycle extension
plot_cycle(P, Q, cycle = cycle_W_PQ)

<!DOCTYPE html>
 
 
 Plots.jl

# 4. Find corresponding cycle in `W(Q,P)` via Dowker's Theorem

In [16]:
# find corresponding cycle
cycle_W_QP = find_Dowker_cycle_correspondence(cycle_W_PQ, param, D_P_Q);

In [17]:
# plot corresponding cycle 
plot_cycle(P, Q, cycle = cycle_W_QP, cycle_loc = "Q")

<!DOCTYPE html>
 
 
 Plots.jl

# 5. Run the extension method from `W(Q,P)` to `VR(Q)`

Find parameter at which to run the extension method.
We'll choose the parameter immediately prior to the death time of `cycle_W_QP`.

In [18]:
# choose parameter
parameter = find_cycle_death_in_Witness(cycle_W_QP, W_Q)
psi = maximum(D_Q_P[D_Q_P.< parameter])

2.7402078205570906

In [19]:
# run extension
extension_to_VR_Q = run_extension_W_to_VR(W = W_Q,
                                          W_cycle = cycle_W_QP,
                                          psi = psi,
                                          C_VR = VR_Q,
                                          D_VR = D_Q);

### Explore results of the second extension method.

In [20]:
plot_pY(extension_to_VR_Q)

<!DOCTYPE html>
 
 
 Plots.jl

In [21]:
p = return_extension_results_at_parameter(extension_to_VR_Q)

*** Parameter key, value pair *** 
key: 1 parameter: 0.385555 
key: 2 parameter: 0.385939 
key: 3 parameter: 0.391274 
key: 4 parameter: 0.393032 
key: 5 parameter: 0.394120 
key: 6 parameter: 0.399924 
key: 7 parameter: 0.400068 
key: 8 parameter: 0.401961 
key: 9 parameter: 0.403550 
key: 10 parameter: 0.406446 
key: 11 parameter: 0.406728 
key: 12 parameter: 0.411214 
key: 13 parameter: 0.412319 
key: 14 parameter: 0.413642 
key: 15 parameter: 0.417098 
key: 16 parameter: 0.418619 
key: 17 parameter: 0.423810 
key: 18 parameter: 0.426529 
key: 19 parameter: 0.432492 
key: 20 parameter: 0.434098 
key: 21 parameter: 0.435042 
key: 22 parameter: 0.439721 
key: 23 parameter: 0.442225 
key: 24 parameter: 0.442342 
key: 25 parameter: 0.448991 
key: 26 parameter: 0.449746 
key: 27 parameter: 0.450233 
key: 28 parameter: 0.450587 
key: 29 parameter: 0.451864 
key: 30 parameter: 0.453054 
key: 31 parameter: 0.453687 
key: 32 parameter: 0.454113 
key: 33 parameter: 0.456991 
key: 34 parameter


Select a key for parameter 1


Selected parameter: 0.3855550508697739

Baseline bars extension at selected parameter: [204]

*** Offset bar extensions at selected parameter *** 
key: 1 offset bar extension: [57]
key: 2 offset bar extension: [12]
key: 3 offset bar extension: [58]
key: 4 offset bar extension: [161]
key: 5 offset bar extension: [160]
key: 6 offset bar extension: [54]
key: 7 offset bar extension: [59]
key: 8 offset bar extension: [56]
key: 9 offset bar extension: [162]
key: 10 offset bar extension: [52]



Select keys for offset bar extensions. 
Leave blank to select none. 
To select multiple keys, separate keys with space. ex) 1 2 3 :  



Baseline bars extension at selected parameter: [204]


<!DOCTYPE html>
 
 
 Plots.jl

# 6. Explore extensions under fixed interval decompositions of `barcode(VR(Q))`.

* Find all cycle extensions and bar extensions at a specific parameter.

In [22]:
# select parameter
param = extension_to_VR_Q["nontrivial_pY"][1]
CE_param, BE_param = find_CE_BE_at_param(extension_to_VR_Q, param);

<b> plot cycle extensions to `barcode(VR(Q))`</b>

In [23]:
@printf("number of cycle extensions at parameter %.4f : %i", param, length(CE_param))

number of cycle extensions at parameter 0.3856 : 1024

In [24]:
# plot a cycle extension at selected parameter
idx = 0
p = plot_cycle(P, Q, cycle = CE_param[idx], cycle_loc = "Q", title = "cycle extension",
                            P_markersize = 5, Q_markersize = 5; legend = false)

<!DOCTYPE html>
 
 
 Plots.jl

Plot the <b>bar extensions</b> at given parameter.
* Select a cycle extension 
* Find and plot the corresponding bar extensions

In [26]:
# select parameter 
@printf("number of cycle extensions at parameter %.4f : %i", param, length(CE_param))

number of cycle extensions at parameter 0.3856 : 1024

In [27]:
# select cycle extension 
y= 0

# find the corresponding bar extension
be = BE_param[y]

# plot the bar extension
barcode_VR_Q = barcode(VR_Q, dim = dim)
p = plot_barcode(barcode_VR_Q, title = "selected bar extension to barcode(VR(Q))", lw = 2, selected_bars = be, epsilon= param, v_line = [param])
plot(p, size = (500, 300))

<!DOCTYPE html>
 
 
 Plots.jl

Plot a summary analogous bars plot under fixed interval decomposition of `barcode(VR(Q))`

In [28]:
# plot the summary
l = grid(4,1)
p1 = plot_barcode(barcode_VR_P, lw = 3, selected_bars = [VR_P_class], title = "Barcode(VR(P))", titlefontsize = 12)
p2 = plot_barcode(barcode_W_P , lw = 3, title = "Barcode(W(P,Q))", titlefontsize = 12)
p3 = plot_barcode(barcode_W_Q, lw = 3, title = "Barcode(W(Q,P))", titlefontsize = 12)
p4 = plot_barcode(barcode_VR_Q, lw = 2, title = "Barcode(VR(Q))", titlefontsize = 12, selected_bars = be)
plot(p1, p2, p3, p4, layout = l, size = (500, 800))


<!DOCTYPE html>
 
 
 Plots.jl

# 7. Explore alternative bar extensions under all possible interval decompositions of `barcode(VR(Q))`.

* Up to this point, the bar extension result has been obtained for some fixed interval decomposition of `barcode(VR(Q))`.
* In this section, we show how to find the bar extensions under all possible interval decompositions. Given `cycle_W_QP` (corresponds to $[\sigma] \in E(\tau, W^\bullet_{Q,P})$ in the paper), the goal is to find $S([\sigma], X^\bullet_Q)$ from Algorithm 6 of paper. We'll refer to this set as <b>alternative bar extensions</b> since these arise from alternative choices of the interval decompositions.
* There are three different methods for exploring the alternative bar extensions. The appropriate tool depends on the sizes of the barcodes of the auxiliary filtration and the target filtration. 

1. Find all alternative bar extensions for all parameters.  
    * This is recommended for data with small barcodes. 
    * This finds the full $S([\sigma], Y^{\bullet}) = \{ S^{\mathcal{D} \circ L^{-1}}_{[y]} | \ell \in p_Y, [y] \in \mathfrak{E}_{\ell}, L \in L_Y \}$ in Algorithm 3 of paper.
2. Find alternative bar extensions at specific parameters.  
    * This is recommended for data with medium size barcodes.
    * Given a parameter $\ell$, this method finds $S([\sigma], Y^{\bullet}; \ell) = \{ S^{\mathcal{D} \circ L^{-1}}_{[y]} | [y] \in \mathfrak{E}_{\ell}, L \in L_Y \} $
3. Find alternative bar extensions of a specific bar extension.
    * This is recommended for data with large size barcodes.
    * Given a selected parameter $\ell$ and cycle extension $[y] \in \mathfrak{E}_{\ell}$, this method finds $\{S^{\mathcal{D} \circ L^{-1}}_{[y]} | L \in L_Y \}$. 
    
For this example, we'll implement method 3 due to the large number of bars `barcode(VR(Q))`. For example implementations of methods 1 and 2, see notebook `EXAMPLE_EXTENSION_VR_VR.ipynb`


In [29]:
# select a parameter and bar extension of interest
param = extension_to_VR_Q["nontrivial_pY"][1]

0.3855550508697739

Select a bar of interest

In [30]:
# find all bar extensions (under fixed interval decomposition of C_Y) at given parameter
CE_param, BE_param = find_CE_BE_at_param(extension_to_VR_Q, param);
@printf("number of bar extensions at parameter %.4f : %i", param, length(BE_param))

number of bar extensions at parameter 0.3856 : 1024

In [32]:
# select bar extension of interest
bar_ext = BE_param[0]

1-element Array{Int64,1}:
 204

In [33]:
# find alternative representations of the selected bar extension
alt_bar_ext = find_alternative_bar_extension(extension_to_VR_Q, param, bar_extension = bar_ext)

1024-element Array{Array{Int64,1},1}:
 [204]
 [12, 204]
 [52, 204]
 [54, 204]
 [56, 204]
 [57, 204]
 [58, 204]
 [59, 204]
 [160, 204]
 [161, 204]
 [162, 204]
 [12, 52, 204]
 [12, 54, 204]
 ⋮
 [54, 56, 57, 58, 59, 160, 161, 162, 204]
 [12, 52, 54, 56, 57, 58, 59, 160, 161, 204]
 [12, 52, 54, 56, 57, 58, 59, 160, 162, 204]
 [12, 52, 54, 56, 57, 58, 59, 161, 162, 204]
 [12, 52, 54, 56, 57, 58, 160, 161, 162, 204]
 [12, 52, 54, 56, 57, 59, 160, 161, 162, 204]
 [12, 52, 54, 56, 58, 59, 160, 161, 162, 204]
 [12, 52, 54, 57, 58, 59, 160, 161, 162, 204]
 [12, 52, 56, 57, 58, 59, 160, 161, 162, 204]
 [12, 54, 56, 57, 58, 59, 160, 161, 162, 204]
 [52, 54, 56, 57, 58, 59, 160, 161, 162, 204]
 [12, 52, 54, 56, 57, 58, 59, 160, 161, 162, 204]

In [34]:
# plot one of the alternative bar extensions

# select an alternative bar extension
alt = alt_bar_ext[2]
barcode_Y = barcode(extension_to_VR_Q["C_VR"], dim = dim)
p =plot_barcode(barcode_Y, selected_bars = alt, lw = 2,
                    epsilon = param, v_line = [param],
                    title = "alternative bar extensions")
plot(p)

<!DOCTYPE html>
 
 
 Plots.jl

# 8. Alternative parameter choice for second extension from `W(Q,P)` to `VR(Q)`

Recall that we have already selected the cycle `cycle_W_QP`. 
From section 6, note that the cycle extension seemed to go around only the right circle, instead of going around both circles of the double torus. 
In this section, we experiment with the parameter at which one runs the second extension method. One will see that choosing an earlier parameter allows the algorithm to find the cycle extensions which goes around both circles. 

In [25]:
# choose parameter
parameter = find_cycle_death_in_Witness(cycle_W_QP, W_Q)
old_psi = maximum(D_Q_P[D_Q_P.< parameter])

2.7402078205570906

In [30]:
# plot Witness barcode and the old parameter
p = plot_barcode(barcode_W_Q, lw = 3, title = "Barcode(W(Q,P))", v_line = [old_psi], titlefontsize = 12)
plot(p)

<!DOCTYPE html>
 
 
 Plots.jl

Let's choose an earlier parameter. In particular, let's choose the parameter immediately prior to the death time of bar 2

In [35]:
# select new parameter
death_bar2 = barcode_W_Q[2,2]
new_psi = maximum(D_Q_P[D_Q_P.< death_bar2])

2.7126178604280877

In [36]:
# run extension
extension_to_VR_Q_new = run_extension_W_to_VR(W = W_Q,
                                          W_cycle = cycle_W_QP,
                                          psi = new_psi,
                                          C_VR = VR_Q,
                                          D_VR = D_Q);

Get example baseline bar extension

In [41]:
p = return_extension_results_at_parameter(extension_to_VR_Q_new)

*** Parameter key, value pair *** 
key: 1 parameter: 0.491979 
key: 2 parameter: 0.492857 
key: 3 parameter: 0.493402 
key: 4 parameter: 0.498616 
key: 5 parameter: 0.499785 
key: 6 parameter: 0.500866 
key: 7 parameter: 0.501318 
key: 8 parameter: 0.501528 
key: 9 parameter: 0.502300 
key: 10 parameter: 0.503181 
key: 11 parameter: 0.507362 
key: 12 parameter: 0.508193 
key: 13 parameter: 0.508786 
key: 14 parameter: 0.511960 
key: 15 parameter: 0.516230 
key: 16 parameter: 0.522816 
key: 17 parameter: 0.529499 
key: 18 parameter: 0.529712 
key: 19 parameter: 0.532798 
key: 20 parameter: 0.533191 
key: 21 parameter: 0.534478 
key: 22 parameter: 0.535141 
key: 23 parameter: 0.538491 
key: 24 parameter: 0.539352 
key: 25 parameter: 0.541320 
key: 26 parameter: 0.543566 
key: 27 parameter: 0.543925 
key: 28 parameter: 0.547271 
key: 29 parameter: 0.550217 
key: 30 parameter: 0.551373 
key: 31 parameter: 0.552791 
key: 32 parameter: 0.552866 
key: 33 parameter: 0.561103 
key: 34 parameter


Select a key for parameter 1


Selected parameter: 0.49197920873656

Baseline bars extension at selected parameter: [204, 208]

*** Offset bar extensions at selected parameter *** 
key: 1 offset bar extension: [80]
key: 2 offset bar extension: [85]
key: 3 offset bar extension: [83]
key: 4 offset bar extension: [18]
key: 5 offset bar extension: [72]
key: 6 offset bar extension: [197]
key: 7 offset bar extension: [168]
key: 8 offset bar extension: [188]
key: 9 offset bar extension: [86]
key: 10 offset bar extension: [75]
key: 11 offset bar extension: [91]
key: 12 offset bar extension: [89]
key: 13 offset bar extension: [54]
key: 14 offset bar extension: [160]
key: 15 offset bar extension: [94]
key: 16 offset bar extension: [90]
key: 17 offset bar extension: [62]
key: 18 offset bar extension: [82]
key: 19 offset bar extension: [84]
key: 20 offset bar extension: [77]
key: 21 offset bar extension: [60]
key: 22 offset bar extension: [165]
key: 23 offset bar extension: [167]
key: 24 offset bar extension: [187]
key: 25 offs


Select keys for offset bar extensions. 
Leave blank to select none. 
To select multiple keys, separate keys with space. ex) 1 2 3 :  



Baseline bars extension at selected parameter: [204, 208]


<!DOCTYPE html>
 
 
 Plots.jl

Plot cycle representatives of the selected baseline extension

In [43]:
# selected ext
bar_ext = [204, 208]

2-element Array{Int64,1}:
 204
 208

In [49]:
bar_ext_cycle = get_multiclass_cyclerep(VR_Q, bar_ext);
plot_cycle(P, Q, cycle = bar_ext_cycle, cycle_loc = "Q")

<!DOCTYPE html>
 
 
 Plots.jl

When we run the second extension method with this new parameter, the baseline bar extension consists of two bars. The corresponding cycle representative shows a cycle that goes around both circles of the double torus.